### Contents

[Imports](#Imports)

[bottom](#bottom)

### Imports

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
from os.path import join as pjoin
import sys 
from pathlib import Path
sys.path.insert(0, str(Path(os.getcwd()).parent))
import json 
import itertools 
from pprint import pprint
from datetime import datetime, date, timedelta
import requests 
import time
from pprint import pprint
import json 

import pandas as pd
from tqdm import tqdm
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
from fabulous import color as fb_color
from PIL import Image
from io import BytesIO
%matplotlib inline

from IPython.display import display, clear_output

In [3]:
ROOT_PATH = str(Path(os.getcwd()).parent)

In [5]:
from src.parse_utils import (
    get_catalog,
    find_card_url,
    get_images_urls_from_card_url
)
from src.utils import (
    get_uniq_items_with_images,
)

In [6]:
matplotlib.rcParams['figure.figsize'] = (7, 7)
sns.set_style('whitegrid')

---

In [7]:
catalog = get_catalog()
pprint(catalog)

[{'id': 1234, 'name': 'Сертификаты Wildberries', 'url': '/gift/certificates'},
 {'childs': [{'id': 8126,
              'name': 'Блузки и рубашки',
              'parent': 306,
              'query': 'cat=8126',
              'seo': 'Женские блузки и рубашки',
              'shard': 'bl_shirts',
              'url': '/catalog/zhenshchinam/odezhda/bluzki-i-rubashki'},
             {'id': 8127,
              'name': 'Брюки',
              'parent': 306,
              'query': 'cat=8127',
              'seo': 'Женские брюки',
              'shard': 'pants',
              'url': '/catalog/zhenshchinam/odezhda/bryuki-i-shorty'},
             {'id': 63010,
              'name': 'Верхняя одежда',
              'parent': 306,
              'query': 'cat=63010',
              'seo': 'Верхняя женская одежда',
              'shard': 'outwear1',
              'url': '/catalog/zhenshchinam/odezhda/verhnyaya-odezhda'},
             {'id': 8130,
              'name': 'Джемперы, водолазки и кардиганы',

In [8]:
all_urls = json.load(open(
    pjoin(ROOT_PATH, 'raw_data/all_urls_tmp.json')
))
print(f"{len(all_urls):,}")
print(f"{len([category_info for category_info in all_urls if category_info.get('products') is not None]):,}")

2,398
1,621


In [9]:
idxs = [idx for idx, category in enumerate(all_urls) if 'adult' in str(category.get('shard'))]
idxs
[category for idx, category in enumerate(all_urls) if idx in idxs]

[{'category_id': 8174,
  'name': 'Белье и аксессуары',
  'shard': 'adult1',
  'query': 'cat=8174',
  'url': 'https://catalog.wb.ru/catalog/adult1/v2/catalog?ab_testing=false&appType=1&curr=rub&dest=-446116&sort=popular&spp=30&uclusters=0&cat=8174',
  'products': {'193106607': {'card_url': 'https://basket-13.wbbasket.ru/vol1931/part193106/193106607/info/ru/card.json',
    'item_images_urls': ['https://basket-13.wbbasket.ru/vol1931/part193106/193106607/images/big/1.webp',
     'https://basket-13.wbbasket.ru/vol1931/part193106/193106607/images/big/2.webp',
     'https://basket-13.wbbasket.ru/vol1931/part193106/193106607/images/big/3.webp',
     'https://basket-13.wbbasket.ru/vol1931/part193106/193106607/images/big/4.webp',
     'https://basket-13.wbbasket.ru/vol1931/part193106/193106607/images/big/5.webp',
     'https://basket-13.wbbasket.ru/vol1931/part193106/193106607/images/big/6.webp',
     'https://basket-13.wbbasket.ru/vol1931/part193106/193106607/images/big/7.webp']},
   '193023941

In [46]:
# items_metadata = {}
# browse_result_items = json.loads(requests.get(all_urls[idxs[0]]['url']).content)
# for i, item_metadata in tqdm(enumerate(browse_result_items['data']['products'], start=1)):
#     if i % 15 == 0:
#         time.sleep(10)
#     item_id = item_metadata['id']
#     card_url, success_flag = find_card_url(
#         item_id=item_id,
#         max_retries=40,
#         sleep_time=0.1,
#         verbose=False,
#         start_basket_number=10,
#         max_basket_number=30
#     )
#     if success_flag:
#         items_metadata[item_id] = {'card_url': card_url}
#         item_images_urls = get_images_urls_from_card_url(
#             card_url=card_url,
#             n_images=None,
#             verify=True
#         )
#         items_metadata[item_id]['item_images_urls'] = item_images_urls
# pprint(items_metadata)

# # json.dump(items_metadata, open('./raw_data/browse_category.json', mode='w', encoding='utf-8'))

100it [02:59,  1.79s/it]

{2565970: {'card_url': 'https://basket-01.wbbasket.ru/vol25/part2565/2565970/info/ru/card.json',
           'item_images_urls': ['https://basket-01.wbbasket.ru/vol25/part2565/2565970/images/big/1.webp',
                                'https://basket-01.wbbasket.ru/vol25/part2565/2565970/images/big/2.webp',
                                'https://basket-01.wbbasket.ru/vol25/part2565/2565970/images/big/3.webp',
                                'https://basket-01.wbbasket.ru/vol25/part2565/2565970/images/big/4.webp',
                                'https://basket-01.wbbasket.ru/vol25/part2565/2565970/images/big/5.webp',
                                'https://basket-01.wbbasket.ru/vol25/part2565/2565970/images/big/6.webp',
                                'https://basket-01.wbbasket.ru/vol25/part2565/2565970/images/big/7.webp',
                                'https://basket-01.wbbasket.ru/vol25/part2565/2565970/images/big/8.webp',
                                'https://basket-01.wbba

In [18]:
from src.ml.utils import (
    ImageEncoder,
    encode_images
)

In [13]:
image_encoder = ImageEncoder(model_str='google/vit-base-patch16-224-in21k')
image_encoder.encode(image_url='https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/1.webp')

initializing ImageEncoder...
ok


array([ 1.16129816e-01, -7.97767341e-02,  3.11706841e-01, -1.84357971e-01,
        3.52522731e-01, -2.29039043e-01, -5.19799888e-02,  1.73537627e-01,
        2.19617158e-01, -2.17173137e-02, -3.53218526e-01,  1.07998192e-01,
       -5.57878474e-03, -1.26852944e-01, -2.50834711e-02, -2.08107650e-01,
        8.80188197e-02, -5.76843545e-02,  6.59254789e-02, -2.79149767e-02,
        1.09192289e-01, -2.37345591e-01,  9.08755139e-02, -8.52581188e-02,
        1.21816620e-01, -1.40245140e-01,  6.98255301e-02, -1.06283739e-01,
       -1.55464530e-01, -1.14111438e-01,  2.01131761e-01, -5.81400841e-02,
        1.86530694e-01, -8.00571963e-02,  1.30725414e-01,  2.24788368e-01,
        1.40932441e-01,  3.57788146e-01,  6.54344186e-02, -3.09994407e-02,
        1.48303002e-01,  2.94549763e-01,  8.12367499e-02,  3.33929121e-01,
       -3.12284917e-01,  1.05604708e-01,  2.54594177e-01, -3.17888975e-01,
        1.21808730e-01, -2.78478265e-01, -2.99536139e-01, -7.26858154e-04,
       -3.18446234e-02, -

In [14]:
uniq_items_with_images = get_uniq_items_with_images(
    flatten_categories=all_urls,
    verbose=True
)
print(f"{len(uniq_items_with_images):,}")
pprint({k: v for i, (k, v) in enumerate(uniq_items_with_images.items()) if i <= 2})

flatten_categories: 100%|██████████| 2398/2398 [00:00<00:00, 25744.70it/s]

117,308
{'10147914': ['https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/1.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/2.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/3.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/4.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/5.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/6.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/7.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/8.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/9.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big/10.webp',
              'https://basket-01.wbbasket.ru/vol101/part10147/10147914/images/big

In [17]:
image_encoder = ImageEncoder(model_str='google/vit-base-patch16-224-in21k')

images_embeddings = encode_images(
    images_urls={item_id: images_urls_list for i, (item_id, images_urls_list) in enumerate(uniq_items_with_images.items()) if i <= 5},
    encoder_model=image_encoder,
    verbose=True
)
images_embs_array = np.array([
    emb 
    for item_id, item_image_emb_dict in images_embeddings.items() 
        for image_number, emb in item_image_emb_dict.items()
])
print(f"{len(images_embeddings):,}")
pprint(images_embeddings)

initializing ImageEncoder...
ok


100%|██████████| 6/6 [01:59<00:00, 19.98s/it]


6
{'10147914': {1: array([ 8.68406296e-02, -7.39764720e-02, -1.65750250e-01,  2.77694911e-01,
        4.32136357e-02, -2.84162253e-01, -1.43248647e-01,  9.14499611e-02,
        6.93479702e-02,  2.29205057e-01, -1.56500801e-01,  1.31643742e-01,
        1.43579869e-02,  1.70146730e-02,  1.51082026e-02, -8.84202048e-02,
        2.32519701e-01,  6.03582337e-02,  2.07410812e-01, -2.31377125e-01,
       -2.74654925e-01,  1.62576690e-01, -1.78765982e-01,  2.70680040e-02,
       -9.25945789e-02,  4.02192734e-02, -8.03916156e-02,  4.26337011e-02,
        9.76835713e-02, -9.40180495e-02, -6.07400462e-02,  2.16352284e-01,
       -2.43934587e-01, -2.98117906e-01,  5.02136350e-03, -6.93180263e-02,
       -2.00462326e-01,  1.95576340e-01, -1.83048144e-01, -3.31975847e-01,
       -2.00877130e-01,  1.25121817e-01,  3.87796909e-02,  2.76938379e-01,
       -2.49824643e-01,  2.39521772e-01, -1.23493612e-01, -7.91021734e-02,
       -4.02546465e-01, -1.05339754e-02,  2.08872542e-01, -7.76268020e-02,
      

In [33]:
def cosine_similarity(a: np.ndarray, b: np.ndarray) -> float:
    return ((a @ b) / (np.linalg.norm(a) * np.linalg.norm(b))).item()

In [ ]:
'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/1.webp',
'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/2.webp',
'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/3.webp',
'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/4.webp',
'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/5.webp',
'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/6.webp',
'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/7.webp',
'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/8.webp'


'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/1.webp',
'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/2.webp',
'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/3.webp',
'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/4.webp',
'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/5.webp',
'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/6.webp',
'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/7.webp',
'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/8.webp',
'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/9.webp'

In [52]:
cosine_similarity(
    a=(model(
        **processor(images=Image.open(requests.get(
            'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/1.webp', 
            stream=True
        ).raw).convert("RGB"), return_tensors="pt")
    )
    .last_hidden_state[0][0].detach().numpy()),
    b=(model(
        **processor(images=Image.open(requests.get(
            'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/2.webp', 
            stream=True
        ).raw).convert("RGB"), return_tensors="pt")
    )
    .last_hidden_state[0][0].detach().numpy())
)

0.7537326812744141

In [53]:
cosine_similarity(
    a=(model(
        **processor(images=Image.open(requests.get(
            'https://basket-10.wbbasket.ru/vol1572/part157295/157295096/images/big/1.webp', 
            stream=True
        ).raw).convert("RGB"), return_tensors="pt")
    )
    .last_hidden_state[0][0].detach().numpy()),
    b=(model(
        **processor(images=Image.open(requests.get(
            'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/1.webp', 
            stream=True
        ).raw).convert("RGB"), return_tensors="pt")
    )
    .last_hidden_state[0][0].detach().numpy())
)

0.527221143245697

In [54]:
cosine_similarity(
    a=(model(
        **processor(images=Image.open(requests.get(
            'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/2.webp', 
            stream=True
        ).raw).convert("RGB"), return_tensors="pt")
    )
    .last_hidden_state[0][0].detach().numpy()),
    b=(model(
        **processor(images=Image.open(requests.get(
            'https://basket-12.wbbasket.ru/vol1717/part171752/171752342/images/big/1.webp', 
            stream=True
        ).raw).convert("RGB"), return_tensors="pt")
    )
    .last_hidden_state[0][0].detach().numpy())
)

0.8011552691459656

### bottom